In [1]:
import pandas as pd
import numpy as np

from sklearn import datasets
from sklearn.linear_model import Ridge
from sklearn.linear_model import BayesianRidge
from sklearn.metrics import r2_score
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler

import keras
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasRegressor

In [2]:
# SELECCIÓN DEL MODELO Y ENTRENAMIENTO

# Lectura del dataset

dataset = pd.read_csv('C:/Users/toled/OneDrive/Documentos/MATEMÁTICAS/TFG/Dataset NBA.csv',sep=";", encoding="ISO 8859-1")
dataset = dataset.drop('YEAR', 1)
dataset = dataset.drop('Team', 1)
dataset = dataset.drop('Arena', 1)
dataset = dataset.drop('Champion', 1)
dataset = dataset.drop('Attend.', 1)
dataset = dataset.drop('W%', 1)
dataset = dataset.drop('L%', 1)
dataset = dataset.drop('PL', 1)

dataset.head()

C:\Users\toled\AppData\Local\Temp/ipykernel_14276/2628121264.py:6: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('YEAR', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_14276/2628121264.py:7: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('Team', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_14276/2628121264.py:8: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('Arena', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_14276/2628121264.py:9: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  dataset = dataset.drop('Champion', 1)
C:\Users\toled\AppData\Local\Temp/ipykernel_14276/262812126

G     MP    FG   FGA   FG%    3P   3PA   3P%    2P   2PA  ...  3PAr   TS%  \
0  82  240.3  41.5  88.3  47.0  12.9  34.4  37.4  28.6  53.9  ...   390  58.1   
1  82  240.6  41.7  85.6  48.7   1.5   5.0  30.2  40.2  80.6  ...    59  54.7   
2  82  242.7  42.6  91.2  46.7   2.6   8.2  31.3  40.0  83.0  ...    90  51.9   
3  82  242.7  34.9  78.5  44.4   4.9  13.9  35.2  30.0  64.5  ...   177  52.7   
4  82  242.1  42.0  86.8  48.4   0.9   2.9  31.1  41.1  84.0  ...    33  53.6   

   OFeFG%  OfTOV%  ORB%  Of FT/FGA  DEFeFG%  DefTOV%  DRB%  Def FT/FGA  
0    54.3    10.8  23.0        205     54.3     11.5  76.9         177  
1    49.6    13.5  36.3        277     50.9     14.0  65.5         254  
2    48.1    13.0  33.6        203     49.7     13.2  68.3         209  
3    47.6    15.7  27.9        248     46.9     12.1  70.4         222  
4    48.9    15.3  32.5        250     48.5     15.2  63.8         249  

[5 rows x 42 columns]

In [8]:
# Preprocesado

# Se separa la columna a predecir
X = dataset.iloc[:,dataset.columns != 'PW']
y = dataset.iloc[:,25]

# En este ejemplo, se reescalan con un MinMaxScaler
sc = MinMaxScaler()
sc.fit(X) # Se ajusta el reescalador
X = sc.transform(X)

print(X)
print(y)
y.shape

[[1.         0.06122449 0.60451977 ... 0.13793103 0.76616915 0.10526316]
 [1.         0.12244898 0.61581921 ... 0.42528736 0.19900498 0.51052632]
 [1.         0.55102041 0.66666667 ... 0.33333333 0.33830846 0.27368421]
 ...
 [1.         0.36734694 0.31073446 ... 0.55172414 0.46766169 0.52105263]
 [1.         0.36734694 0.37288136 ... 0.47126437 0.47263682 0.48421053]
 [0.6875     0.34693878 0.70056497 ... 0.25287356 0.80099502 0.31578947]]
0       0.548780
1       0.536585
2       0.451220
3       0.378049
4       0.451220
          ...   
1189    0.487805
1190    0.524390
1191    0.560976
1192    0.487805
1193    0.444444
Name: PW, Length: 1194, dtype: float64


(1194,)

In [4]:
# Dividir el dataset en train y test

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33)

In [5]:
# SELECCION DE HIPERPARAMETROS POR VALIDACION CRUZADA

# Modelo: Bayesian Ridge

parameters = {'n_iter':[100, 200, 300, 500],\
              'alpha_1':[1e-6, 1e-4, 1e-1, 1], \
              'alpha_2':[1e-4, 1e-10, 1e-1, 1], \
              'lambda_1':[1e-6, 1e-10, 1e-1, 1],\
              'lambda_2':[1e-6, 1e-4]}

bay_ridge = BayesianRidge()
cv = GridSearchCV(bay_ridge, parameters, refit = True, scoring='r2', verbose = 3)
cv.fit(X_train, y_train)

Fitting 5 folds for each of 512 candidates, totalling 2560 fits
[CV 1/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.997 total time=   0.0s
[CV 2/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.996 total time=   0.0s
[CV 3/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.998 total time=   0.0s
[CV 4/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.998 total time=   0.0s
[CV 5/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=100;, score=0.998 total time=   0.0s
[CV 1/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=200;, score=0.997 total time=   0.0s
[CV 2/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=200;, score=0.996 total time=   0.0s
[CV 3/5] END alpha_1=1e-06, alpha_2=0.0001, lambda_1=1e-06, lambda_2=1e-06, n_iter=200;, score=0

GridSearchCV(estimator=BayesianRidge(),
             param_grid={'alpha_1': [1e-06, 0.0001, 0.1, 1],
                         'alpha_2': [0.0001, 1e-10, 0.1, 1],
                         'lambda_1': [1e-06, 1e-10, 0.1, 1],
                         'lambda_2': [1e-06, 0.0001],
                         'n_iter': [100, 200, 300, 500]},
             scoring='r2', verbose=3)

In [7]:
# Mostrar el ranking

pd.DataFrame(cv.cv_results_).sort_values(by=['rank_test_score']).head()

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
428       0.003801  4.004244e-04         0.000400        0.000490   
429       0.003000  6.143617e-07         0.000200        0.000400   
430       0.002999  1.029350e-06         0.000403        0.000494   
431       0.003400  4.897268e-04         0.000600        0.000490   
421       0.003199  3.997576e-04         0.000801        0.000749   

    param_alpha_1 param_alpha_2 param_lambda_1 param_lambda_2 param_n_iter  \
428             1           0.0            0.0         0.0001          100   
429             1           0.0            0.0         0.0001          200   
430             1           0.0            0.0         0.0001          300   
431             1           0.0            0.0         0.0001          500   
421             1           0.0       0.000001         0.0001          200   

                                                params  split0_test_score  \
428  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.996839   
429  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.996839   
430  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.996839   
431  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.996839   
421  {'alpha_1': 1, 'alpha_2': 1e-10, 'lambda_1': 1...           0.996839   

     split1_test_score  split2_test_score  split3_test_score  \
428           0.996357           0.997826           0.997828   
429           0.996357           0.997826           0.997828   
430           0.996357           0.997826           0.997828   
431           0.996357           0.997826           0.997828   
421           0.996357           0.997826           0.997828   

     split4_test_score  mean_test_score  std_test_score  rank_test_score  
428            0.99782         0.997334         0.00062                1  
429            0.99782         0.997334         0.00062                1  
430            0.99782         0.997334         0.00062                1  
431            0.99782         0.997334         0.00062                1  
421            0.99782         0.997334         0.00062                5

In [8]:
# Modelo: Red neuronal

def neural_network(neuronas_capa_1 = 25, neuronas_capa_2 = 15):
    neural_net = Sequential()
    neural_net.add(Dense(neuronas_capa_1, input_dim=X.shape[1], activation='sigmoid'))
    neural_net.add(Dense(neuronas_capa_2, activation='sigmoid'))
    neural_net.add(Dense(1, activation='linear'))

    neural_net.compile(loss='mean_squared_error', optimizer='adam', metrics=['mae'])
    return neural_net

neu_net = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[25, 50, 10], 'neuronas_capa_2':[25, 50, 10], 'batch_size':[20, 30]}

cv = GridSearchCV(neu_net, parameters, refit=True, scoring='r2', verbose= 3)
cv.fit(X_train, y_train)

C:\Users\toled\AppData\Local\Temp/ipykernel_6216/1291393717.py:12: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net = KerasRegressor(build_fn=neural_network, epochs = 500)


Fitting 5 folds for each of 18 candidates, totalling 90 fits
Epoch 1/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0340 - mae: 0.1502
Epoch 2/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0200 - mae: 0.1170
Epoch 3/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0177 - mae: 0.1106
Epoch 4/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0160 - mae: 0.1045
Epoch 5/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0141 - mae: 0.0981
Epoch 6/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0115 - mae: 0.0885
Epoch 7/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0094 - mae: 0.0796
Epoch 8/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0070 - mae: 0.0690
Epoch 9/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0050 - mae: 0.0580
Epoch 10/500
32/32 [==============================] - 0s 1ms/step - loss: 0.0037 - mae: 0.049

GridSearchCV(estimator=<keras.wrappers.scikit_learn.KerasRegressor object at 0x0000026EA83B97C0>,
             param_grid={'batch_size': [20, 30],
                         'neuronas_capa_1': [25, 50, 10],
                         'neuronas_capa_2': [25, 50, 10]},
             scoring='r2', verbose=3)

In [9]:
# Mostrar el ranking

pd.DataFrame(cv.cv_results_).sort_values(by=['rank_test_score']).head()

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
8       27.605178      0.936110         0.083970        0.005255   
17      40.118260      3.826820         0.200942        0.023232   
2       26.163171      1.187569         0.078762        0.007657   
4       26.690020      0.276444         0.083235        0.005459   
6       26.792423      0.449013         0.125148        0.089546   

   param_batch_size param_neuronas_capa_1 param_neuronas_capa_2  \
8                20                    10                    10   
17               30                    10                    10   
2                20                    25                    10   
4                20                    50                    50   
6                20                    10                    25   

                                               params  split0_test_score  \
8   {'batch_size': 20, 'neuronas_capa_1': 10, 'neu...           0.997714   
17  {'batch_size': 30, 'neuronas_capa_1': 10, 'neu...           0.997799   
2   {'batch_size': 20, 'neuronas_capa_1': 25, 'neu...           0.997502   
4   {'batch_size': 20, 'neuronas_capa_1': 50, 'neu...           0.997373   
6   {'batch_size': 20, 'neuronas_capa_1': 10, 'neu...           0.997885   

    split1_test_score  split2_test_score  split3_test_score  \
8            0.997722           0.998688           0.998784   
17           0.996259           0.997967           0.998848   
2            0.998087           0.997768           0.998805   
4            0.997593           0.998104           0.998404   
6            0.997381           0.997430           0.998580   

    split4_test_score  mean_test_score  std_test_score  rank_test_score  
8            0.998064         0.998194        0.000461                1  
17           0.998545         0.997883        0.000897                2  
2            0.996871         0.997806        0.000640                3  
4            0.997453         0.997785        0.000401                4  
6            0.997531         0.997761        0.000446                5

In [10]:
#Mejor modelo

neu_net1 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[10], 'neuronas_capa_2':[10], 'batch_size':[20]}

neu_net1.fit(X_train, y_train)

ml_model1 = neu_net1

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_6216/4051665695.py:3: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net1 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 0s 1ms/step - loss: 0.0334 - mae: 0.1476
Epoch 2/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0200 - mae: 0.1173
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0184 - mae: 0.1121
Epoch 4/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0167 - mae: 0.1071
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0148 - mae: 0.1005
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0130 - mae: 0.0945
Epoch 7/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0111 - mae: 0.0871
Epoch 8/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0095 - mae: 0.0802
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0076 - mae: 0.0719
Epoch 10/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0059 - mae: 0.0632
Epoch 11/500
25/25 [==============================] - 0s 1ms/step - los

In [11]:
# Predecir en test

y_pred1 = ml_model1.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred1)))

R2 obtenido en test: 0.9981447311192162


In [12]:
#Segundo mejor modelo

neu_net2 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[10], 'neuronas_capa_2':[10], 'batch_size':[30]}

neu_net2.fit(X_train, y_train)

ml_model2 = neu_net2

C:\Users\toled\AppData\Local\Temp/ipykernel_6216/1508318198.py:3: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net2 = KerasRegressor(build_fn=neural_network, epochs = 500)


Epoch 1/500
25/25 [==============================] - 1s 2ms/step - loss: 0.1236 - mae: 0.2935
Epoch 2/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0253 - mae: 0.1284
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0217 - mae: 0.1222
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0206 - mae: 0.1190
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0196 - mae: 0.1157
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0185 - mae: 0.1125
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0174 - mae: 0.1093
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0163 - mae: 0.1056
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0151 - mae: 0.1017
Epoch 10/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0140 - mae: 0.0978
Epoch 11/500
25/25 [==============================] - 0s 1m

In [13]:
# Predecir en test

y_pred2 = ml_model2.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred2)))

R2 obtenido en test: 0.9955827394066312


In [14]:
#Tercer mejor modelo

neu_net3 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[25], 'neuronas_capa_2':[10], 'batch_size':[20]}

neu_net3.fit(X_train, y_train)

ml_model3 = neu_net3

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_6216/2321554593.py:3: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net3 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 0s 1ms/step - loss: 0.0319 - mae: 0.1458
Epoch 2/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0247 - mae: 0.1296
Epoch 3/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0224 - mae: 0.1237
Epoch 4/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0201 - mae: 0.1168
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0176 - mae: 0.1093
Epoch 6/500
25/25 [==============================] - 0s 774us/step - loss: 0.0149 - mae: 0.1005
Epoch 7/500
25/25 [==============================] - 0s 969us/step - loss: 0.0122 - mae: 0.0908
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0095 - mae: 0.0797
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0069 - mae: 0.0684
Epoch 10/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0050 - mae: 0.0579
Epoch 11/500
25/25 [==============================] - 0s 1ms/step -

In [15]:
# Predecir en test

y_pred3 = ml_model3.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred3)))

R2 obtenido en test: 0.9981391757887176


In [16]:
#Cuarto mejor modelo

neu_net4 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[50], 'neuronas_capa_2':[50], 'batch_size':[20]}

neu_net4.fit(X_train, y_train)

ml_model4 = neu_net4

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_6216/682387745.py:3: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net4 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 1s 2ms/step - loss: 0.0929 - mae: 0.2496
Epoch 2/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0253 - mae: 0.1284
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0206 - mae: 0.1193
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0190 - mae: 0.1140
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0181 - mae: 0.1115
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0168 - mae: 0.1071
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0156 - mae: 0.1030
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0143 - mae: 0.0988
Epoch 9/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0129 - mae: 0.0939
Epoch 10/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0116 - mae: 0.0889
Epoch 11/500
25/25 [==============================] - 0s 986us/step - l

In [17]:
# Predecir en test

y_pred4 = ml_model4.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred4)))

R2 obtenido en test: 0.9963025798942325


In [18]:
#Quinto mejor modelo

neu_net5 = KerasRegressor(build_fn=neural_network, epochs = 500)

parameters = {'neuronas_capa_1':[10], 'neuronas_capa_2':[25], 'batch_size':[20]}

neu_net5.fit(X_train, y_train)

ml_model5 = neu_net5

Epoch 1/500


C:\Users\toled\AppData\Local\Temp/ipykernel_6216/3607808957.py:3: DeprecationWarning: KerasRegressor is deprecated, use Sci-Keras (https://github.com/adriangb/scikeras) instead. See https://www.adriangb.com/scikeras/stable/migration.html for help migrating.
  neu_net5 = KerasRegressor(build_fn=neural_network, epochs = 500)


25/25 [==============================] - 0s 1ms/step - loss: 0.8078 - mae: 0.8589
Epoch 2/500
25/25 [==============================] - 0s 1ms/step - loss: 0.1043 - mae: 0.2751
Epoch 3/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0225 - mae: 0.1246
Epoch 4/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0217 - mae: 0.1214
Epoch 5/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0210 - mae: 0.1202
Epoch 6/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0207 - mae: 0.1193
Epoch 7/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0203 - mae: 0.1183
Epoch 8/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0199 - mae: 0.1170
Epoch 9/500
25/25 [==============================] - 0s 1ms/step - loss: 0.0195 - mae: 0.1159
Epoch 10/500
25/25 [==============================] - 0s 2ms/step - loss: 0.0191 - mae: 0.1146
Epoch 11/500
25/25 [==============================] - 0s 1ms/step - los

In [19]:
# Predecir en test

y_pred5 = ml_model5.predict(X_test)

# Evaluar el error en test

print('R2 obtenido en test: ' + str(r2_score(y_test, y_pred5)))

R2 obtenido en test: 0.997914665477407
